In [1]:
# Import our dependencies
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,OneHotEncoder
import pandas as pd
import tensorflow as tf

#  Import and read the charity_data.csv.
import pandas as pd 
application_df = pd.read_csv("charity_data.csv")
application_df.head()

EIN                                      NAME APPLICATION_TYPE  \
0  10520599              BLUE KNIGHTS MOTORCYCLE CLUB              T10   
1  10531628    AMERICAN CHESAPEAKE CLUB CHARITABLE TR               T3   
2  10547893        ST CLOUD PROFESSIONAL FIREFIGHTERS               T5   
3  10553066            SOUTHSIDE ATHLETIC ASSOCIATION               T3   
4  10556103  GENETIC RESEARCH INSTITUTE OF THE DESERT               T3   

        AFFILIATION CLASSIFICATION      USE_CASE  ORGANIZATION  STATUS  \
0       Independent          C1000    ProductDev   Association       1   
1       Independent          C2000  Preservation  Co-operative       1   
2  CompanySponsored          C3000    ProductDev   Association       1   
3  CompanySponsored          C2000  Preservation         Trust       1   
4       Independent          C1000     Heathcare         Trust       1   

      INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  IS_SUCCESSFUL  
0              0                      N     5000              1  
1         1-9999                      N   108590              1  
2              0                      N     5000              0  
3    10000-24999                      N     6692              1  
4  100000-499999                      N   142590              1

In [2]:
# Drop the non-beneficial ID columns, 'EIN' and 'NAME'.
application_df = application_df.drop(["EIN", "NAME"], axis=1)
application_df.head()

APPLICATION_TYPE       AFFILIATION CLASSIFICATION      USE_CASE  \
0              T10       Independent          C1000    ProductDev   
1               T3       Independent          C2000  Preservation   
2               T5  CompanySponsored          C3000    ProductDev   
3               T3  CompanySponsored          C2000  Preservation   
4               T3       Independent          C1000     Heathcare   

   ORGANIZATION  STATUS     INCOME_AMT SPECIAL_CONSIDERATIONS  ASK_AMT  \
0   Association       1              0                      N     5000   
1  Co-operative       1         1-9999                      N   108590   
2   Association       1              0                      N     5000   
3         Trust       1    10000-24999                      N     6692   
4         Trust       1  100000-499999                      N   142590   

   IS_SUCCESSFUL  
0              1  
1              1  
2              0  
3              1  
4              1

In [3]:
# Determine the number of unique values in each column.
application_df.nunique()

APPLICATION_TYPE            17
AFFILIATION                  6
CLASSIFICATION              71
USE_CASE                     5
ORGANIZATION                 4
STATUS                       2
INCOME_AMT                   9
SPECIAL_CONSIDERATIONS       2
ASK_AMT                   8747
IS_SUCCESSFUL                2
dtype: int64

### First attempt for > 75% accuracy will be to change the values for APPLICATION_TYPE and CLASSIFICATION bins

In [4]:
# Look at APPLICATION_TYPE value counts for binning
application_counts = application_df.APPLICATION_TYPE.value_counts()
application_counts

T3     27037
T4      1542
T6      1216
T5      1173
T19     1065
T8       737
T7       725
T10      528
T9       156
T13       66
T12       27
T2        16
T14        3
T25        3
T29        2
T15        2
T17        1
Name: APPLICATION_TYPE, dtype: int64

In [5]:
# Determine which values to replace if counts are less than ...?
# First attempt was < 500, will do try < 100
replace_application = list(application_counts[application_counts < 100].index)

# Replace in dataframe
for app in replace_application:
    application_df.APPLICATION_TYPE = application_df.APPLICATION_TYPE.replace(app,"Other")
    
# Check to make sure binning was successful
application_df.APPLICATION_TYPE.value_counts()

T3       27037
T4        1542
T6        1216
T5        1173
T19       1065
T8         737
T7         725
T10        528
T9         156
Other      120
Name: APPLICATION_TYPE, dtype: int64

- Original Other = 276
- First Attempt Other = 120

In [6]:
# Look at CLASSIFICATION value counts for binning
classification_counts = application_df.CLASSIFICATION.value_counts()
classification_counts

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
         ...  
C1370        1
C1283        1
C1900        1
C5200        1
C2500        1
Name: CLASSIFICATION, Length: 71, dtype: int64

In [7]:
print(len(list(classification_counts[classification_counts < 1800].index)), len(list(classification_counts[classification_counts < 1500].index)), 
len(list(classification_counts[classification_counts < 1200].index)), len(list(classification_counts[classification_counts < 900].index)), 
len(list(classification_counts[classification_counts < 600].index)), len(list(classification_counts[classification_counts < 300].index)), len(list(classification_counts[classification_counts < 200].index)) )

66 66 66 66 65 65 64


In [8]:
# Determine which values to replace if counts are less than ..?
# Original was < 1800
# went through by 300s, will try 600
replace_class = list(classification_counts[classification_counts < 600].index)

# Replace in dataframe
for cls in replace_class:
    application_df.CLASSIFICATION = application_df.CLASSIFICATION.replace(cls,"Other")
    
# Check to make sure binning was successful
application_df.CLASSIFICATION.value_counts()

C1000    17326
C2000     6074
C1200     4837
C3000     1918
C2100     1883
Other     1484
C7000      777
Name: CLASSIFICATION, dtype: int64

- Original Other = 2261
- First Other = 1484

In [9]:
# Generate our categorical variable lists
application_cat = application_df.dtypes[application_df.dtypes == "object"].index.tolist()
application_cat

['APPLICATION_TYPE',
 'AFFILIATION',
 'CLASSIFICATION',
 'USE_CASE',
 'ORGANIZATION',
 'INCOME_AMT',
 'SPECIAL_CONSIDERATIONS']

In [10]:
# Create a OneHotEncoder instance
enc = OneHotEncoder(sparse=False)

# Fit and transform the OneHotEncoder using the categorical variable list
encode_df = pd.DataFrame(enc.fit_transform(application_df[application_cat]))

# Add the encoded variable names to the dataframe
encode_df.columns = enc.get_feature_names(application_cat)
encode_df.head()

APPLICATION_TYPE_Other  APPLICATION_TYPE_T10  APPLICATION_TYPE_T19  \
0                     0.0                   1.0                   0.0   
1                     0.0                   0.0                   0.0   
2                     0.0                   0.0                   0.0   
3                     0.0                   0.0                   0.0   
4                     0.0                   0.0                   0.0   

   APPLICATION_TYPE_T3  APPLICATION_TYPE_T4  APPLICATION_TYPE_T5  \
0                  0.0                  0.0                  0.0   
1                  1.0                  0.0                  0.0   
2                  0.0                  0.0                  1.0   
3                  1.0                  0.0                  0.0   
4                  1.0                  0.0                  0.0   

   APPLICATION_TYPE_T6  APPLICATION_TYPE_T7  APPLICATION_TYPE_T8  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   APPLICATION_TYPE_T9  ...  INCOME_AMT_1-9999  INCOME_AMT_10000-24999  \
0                  0.0  ...                0.0                     0.0   
1                  0.0  ...                1.0                     0.0   
2                  0.0  ...                0.0                     0.0   
3                  0.0  ...                0.0                     1.0   
4                  0.0  ...                0.0                     0.0   

   INCOME_AMT_100000-499999  INCOME_AMT_10M-50M  INCOME_AMT_1M-5M  \
0                       0.0                 0.0               0.0   
1                       0.0                 0.0               0.0   
2                       0.0                 0.0               0.0   
3                       0.0                 0.0               0.0   
4                       1.0                 0.0               0.0   

   INCOME_AMT_25000-99999  INCOME_AMT_50M+  INCOME_AMT_5M-10M  \
0                     0.0              0.0                0.0   
1                     0.0              0.0                0.0   
2                     0.0              0.0                0.0   
3                     0.0              0.0                0.0   
4                     0.0              0.0                0.0   

   SPECIAL_CONSIDERATIONS_N  SPECIAL_CONSIDERATIONS_Y  
0                       1.0                       0.0  
1                       1.0                       0.0  
2                       1.0                       0.0  
3                       1.0                       0.0  
4                       1.0                       0.0  

[5 rows x 43 columns]

In [11]:
# Merge one-hot encoded features and drop the originals
application_df = application_df.merge(encode_df, left_index=True, right_index=True)
application_df = application_df.drop(application_cat, axis=1)
application_df.head()

STATUS  ASK_AMT  IS_SUCCESSFUL  APPLICATION_TYPE_Other  \
0       1     5000              1                     0.0   
1       1   108590              1                     0.0   
2       1     5000              0                     0.0   
3       1     6692              1                     0.0   
4       1   142590              1                     0.0   

   APPLICATION_TYPE_T10  APPLICATION_TYPE_T19  APPLICATION_TYPE_T3  \
0                   1.0                   0.0                  0.0   
1                   0.0                   0.0                  1.0   
2                   0.0                   0.0                  0.0   
3                   0.0                   0.0                  1.0   
4                   0.0                   0.0                  1.0   

   APPLICATION_TYPE_T4  APPLICATION_TYPE_T5  APPLICATION_TYPE_T6  ...  \
0                  0.0                  0.0                  0.0  ...   
1                  0.0                  0.0                  0.0  ...   
2                  0.0                  1.0                  0.0  ...   
3                  0.0                  0.0                  0.0  ...   
4                  0.0                  0.0                  0.0  ...   

   INCOME_AMT_1-9999  INCOME_AMT_10000-24999  INCOME_AMT_100000-499999  \
0                0.0                     0.0                       0.0   
1                1.0                     0.0                       0.0   
2                0.0                     0.0                       0.0   
3                0.0                     1.0                       0.0   
4                0.0                     0.0                       1.0   

   INCOME_AMT_10M-50M  INCOME_AMT_1M-5M  INCOME_AMT_25000-99999  \
0                 0.0               0.0                     0.0   
1                 0.0               0.0                     0.0   
2                 0.0               0.0                     0.0   
3                 0.0               0.0                     0.0   
4                 0.0               0.0                     0.0   

   INCOME_AMT_50M+  INCOME_AMT_5M-10M  SPECIAL_CONSIDERATIONS_N  \
0              0.0                0.0                       1.0   
1              0.0                0.0                       1.0   
2              0.0                0.0                       1.0   
3              0.0                0.0                       1.0   
4              0.0                0.0                       1.0   

   SPECIAL_CONSIDERATIONS_Y  
0                       0.0  
1                       0.0  
2                       0.0  
3                       0.0  
4                       0.0  

[5 rows x 46 columns]

- Added 2 rows with bin adjustment, now have 46 columns

In [12]:
application_df.columns

Index(['STATUS', 'ASK_AMT', 'IS_SUCCESSFUL', 'APPLICATION_TYPE_Other',
       'APPLICATION_TYPE_T10', 'APPLICATION_TYPE_T19', 'APPLICATION_TYPE_T3',
       'APPLICATION_TYPE_T4', 'APPLICATION_TYPE_T5', 'APPLICATION_TYPE_T6',
       'APPLICATION_TYPE_T7', 'APPLICATION_TYPE_T8', 'APPLICATION_TYPE_T9',
       'AFFILIATION_CompanySponsored', 'AFFILIATION_Family/Parent',
       'AFFILIATION_Independent', 'AFFILIATION_National', 'AFFILIATION_Other',
       'AFFILIATION_Regional', 'CLASSIFICATION_C1000', 'CLASSIFICATION_C1200',
       'CLASSIFICATION_C2000', 'CLASSIFICATION_C2100', 'CLASSIFICATION_C3000',
       'CLASSIFICATION_C7000', 'CLASSIFICATION_Other',
       'USE_CASE_CommunityServ', 'USE_CASE_Heathcare', 'USE_CASE_Other',
       'USE_CASE_Preservation', 'USE_CASE_ProductDev',
       'ORGANIZATION_Association', 'ORGANIZATION_Co-operative',
       'ORGANIZATION_Corporation', 'ORGANIZATION_Trust', 'INCOME_AMT_0',
       'INCOME_AMT_1-9999', 'INCOME_AMT_10000-24999',
       'INCOME_AMT_1

In [13]:
# Split our preprocessed data into our features and target arrays
X = application_df.drop(['IS_SUCCESSFUL'],axis=1).values
y = application_df['IS_SUCCESSFUL'].values

In [14]:
# Split the preprocessed data into a training and testing dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=78)

In [15]:
# Create a StandardScaler instances
scaler = StandardScaler()

# Fit the StandardScaler
X_scaler = scaler.fit(X_train)

# Scale the data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [16]:
# Define the model - deep neural net, i.e., the number of input features and hidden nodes for each layer.
number_input_features = len(X_train_scaled[0])
hidden_nodes_layer1 = 80
hidden_nodes_layer2 = 30

nn = tf.keras.models.Sequential()

# First hidden layer
nn.add(tf.keras.layers.Dense(units=hidden_nodes_layer1, activation='relu', input_dim=number_input_features))

# Second hidden layer
nn.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation='relu'))

# Output layer
nn.add(tf.keras.layers.Dense(units=1, activation='sigmoid'))

# Check the structure of the model
nn.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 80)                3680      
_________________________________________________________________
dense_1 (Dense)              (None, 30)                2430      
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 31        
Total params: 6,141
Trainable params: 6,141
Non-trainable params: 0
_________________________________________________________________


- Using same number of hidden layers and number of nodes in each
- Since we added 2 feature columns, the parameters for the hidden layers increased

In [17]:
# Import checkpoint dependencies
import os
from tensorflow.keras.callbacks import ModelCheckpoint

# Define the checkpoint path and filenames
os.makedirs("Alphabet_checkpoints/Alphabet_Opt1",exist_ok=True)
checkpoint_path = "Alphabet_checkpoints/Alphabet_Opt1/weights.{epoch:02d}.hdf5"

In [18]:
# Compile the model
nn.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

# Create callback to save model weights every 5 epochs
cp_callback = ModelCheckpoint(
    filepath=checkpoint_path,
    verbose=1,
    save_weights_only=True,
    save_freq = 5
)

In [19]:
# Train the model
fit_model = nn.fit(X_train_scaled,y_train,epochs=100,callbacks=[cp_callback])

Epoch 1/100
  1/804 [..............................] - ETA: 13:59 - loss: 0.6930 - accuracy: 0.6250
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
  6/804 [..............................] - ETA: 9s - loss: 0.6694 - accuracy: 0.6510   
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
 11/804 [..............................] - ETA: 10s - loss: 0.6466 - accuracy: 0.6903
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
 21/804 [..............................] - ETA: 7s - loss: 0.6505 - accuracy: 0.6711 
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
 26/804 [..............................] - ETA: 7s - loss: 0.6367 - accuracy: 0.6863
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
 31/804 [>.............................] - ETA: 8s - loss: 0.6361 - accura

295/804 [==========>...................] - ETA: 6s - loss: 0.5821 - accuracy: 0.7150
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
301/804 [==========>...................] - ETA: 6s - loss: 0.5810 - accuracy: 0.7164
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
310/804 [==========>...................] - ETA: 6s - loss: 0.5813 - accuracy: 0.7158
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
316/804 [==========>...................] - ETA: 6s - loss: 0.5820 - accuracy: 0.7160
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
323/804 [===========>..................] - ETA: 6s - loss: 0.5823 - accuracy: 0.7158
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001:

611/804 [=====================>........] - ETA: 1s - loss: 0.5738 - accuracy: 0.7211
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
621/804 [======================>.......] - ETA: 1s - loss: 0.5736 - accuracy: 0.7213
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
631/804 [======================>.......] - ETA: 1s - loss: 0.5734 - accuracy: 0.7217
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
641/804 [======================>.......] - ETA: 1s - loss: 0.5730 - accuracy: 0.7217
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.01.hdf5
649/804 [=======================>......] - ETA: 1s - loss: 0.5736 - accuracy: 0.7214
Epoch 00001:

112/804 [===>..........................] - ETA: 5s - loss: 0.5589 - accuracy: 0.7235
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
122/804 [===>..........................] - ETA: 5s - loss: 0.5576 - accuracy: 0.7257
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
131/804 [===>..........................] - ETA: 5s - loss: 0.5550 - accuracy: 0.7276
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
135/804 [====>.........................] - ETA: 5s - loss: 0.5560 - accuracy: 0.7273
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
138/804 [====>.........................] - ETA: 5s - loss: 0.5565 - accuracy: 0.7269
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
142/804 [====>.........................] - ETA: 5s - loss: 0.5564 - accuracy: 0.7267
Epoch 000

407/804 [==============>...............] - ETA: 3s - loss: 0.5591 - accuracy: 0.7263
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
417/804 [==============>...............] - ETA: 3s - loss: 0.5588 - accuracy: 0.7268
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
427/804 [==============>...............] - ETA: 3s - loss: 0.5582 - accuracy: 0.7280
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
437/804 [===============>..............] - ETA: 3s - loss: 0.5570 - accuracy: 0.7290
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.02.hdf5
447/804 [=======

...

 79/804 [=>............................] - ETA: 5s - loss: 0.5162 - accuracy: 0.7532
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
 89/804 [==>...........................] - ETA: 5s - loss: 0.5180 - accuracy: 0.7542
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
 99/804 [==>...........................] - ETA: 5s - loss: 0.5205 - accuracy: 0.7522
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
109/804 [===>..........................] - ETA: 5s - loss: 0.5232 - accuracy: 0.7503
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
116/804 [===>..........................] - ETA: 5s - loss: 0.5264 - accuracy: 0.7478
Epoch 00099:

399/804 [=============>................] - ETA: 2s - loss: 0.5341 - accuracy: 0.7413
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
409/804 [==============>...............] - ETA: 2s - loss: 0.5337 - accuracy: 0.7418
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
419/804 [==============>...............] - ETA: 2s - loss: 0.5345 - accuracy: 0.7412
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
429/804 [===============>..............] - ETA: 2s - loss: 0.5353 - accuracy: 0.7405
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
439/804 [=======

714/804 [=========================>....] - ETA: 0s - loss: 0.5349 - accuracy: 0.7411
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
724/804 [==========================>...] - ETA: 0s - loss: 0.5338 - accuracy: 0.7418
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
729/804 [==========================>...] - ETA: 0s - loss: 0.5342 - accuracy: 0.7416
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
739/804 [==========================>...] - ETA: 0s - loss: 0.5333 - accuracy: 0.7424
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.99.hdf5
749/804 [==========================>...] - ETA: 0s - loss: 0.5338 - accuracy: 0.7421
Epoch 00099:

220/804 [=======>......................] - ETA: 4s - loss: 0.5365 - accuracy: 0.7386
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
228/804 [=======>......................] - ETA: 3s - loss: 0.5357 - accuracy: 0.7394
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
236/804 [=======>......................] - ETA: 4s - loss: 0.5351 - accuracy: 0.7409
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
245/804 [========>.....................] - ETA: 4s - loss: 0.5343 - accuracy: 0.7415
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
255/804 [========>.....................] - ETA: 4s - loss: 0.5319 - accuracy: 0.7434
Epoch

533/804 [==================>...........] - ETA: 2s - loss: 0.5305 - accuracy: 0.7434
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
540/804 [===================>..........] - ETA: 1s - loss: 0.5307 - accuracy: 0.7432
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
550/804 [===================>..........] - ETA: 1s - loss: 0.5313 - accuracy: 0.7430
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
560/804 [===================>..........] - ETA: 1s - loss: 0.5316 - accuracy: 0.7428
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt1/weights.100.hdf5
570/804 

In [20]:
# Evaluate the model using the test data
model_loss, model_accuracy = nn.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

268/268 - 1s - loss: 0.5522 - accuracy: 0.7270
Loss: 0.552247941493988, Accuracy: 0.7269970774650574


- First optimization attempt failed with adding another bin to the two categorical variables. The accuracy of the model went down

### Second attempt for > 75% accuracy: 
- Will keep the new bins
- the second attempt will add another hidden layer with 10 nodes

In [21]:
# Define the model - deep neural net, i.e., the number of input features and hidden nodes for each layer.
number_input_features = len(X_train_scaled[0])
hidden_nodes_layer1 = 80
hidden_nodes_layer2 = 30
hidden_nodes_layer3 = 10

nn_new = tf.keras.models.Sequential()

# First hidden layer
nn_new.add(tf.keras.layers.Dense(units=hidden_nodes_layer1, activation='relu', input_dim=number_input_features))

# Second hidden layer
nn_new.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation='relu'))

# Third hidden layer
nn_new.add(tf.keras.layers.Dense(units=hidden_nodes_layer3, activation='relu'))

# Output layer
nn_new.add(tf.keras.layers.Dense(units=1, activation='sigmoid'))

# Check the structure of the model
nn_new.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_3 (Dense)              (None, 80)                3680      
_________________________________________________________________
dense_4 (Dense)              (None, 30)                2430      
_________________________________________________________________
dense_5 (Dense)              (None, 10)                310       
_________________________________________________________________
dense_6 (Dense)              (None, 1)                 11        
Total params: 6,431
Trainable params: 6,431
Non-trainable params: 0
_________________________________________________________________


In [22]:
# Define the checkpoint path and filenames
os.makedirs("Alphabet_checkpoints/Alphabet_Opt2",exist_ok=True)
checkpoint_path = "Alphabet_checkpoints/Alphabet_Opt2/weights.{epoch:02d}.hdf5"

In [23]:
# Compile the model
nn_new.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

# Create callback to save model weights every 5 epochs
cp_callback = ModelCheckpoint(
    filepath=checkpoint_path,
    verbose=1,
    save_weights_only=True,
    save_freq = 5
)

In [24]:
# Train the model
fit_model = nn_new.fit(X_train_scaled,y_train,epochs=100,callbacks=[cp_callback])

Epoch 1/100
  1/804 [..............................] - ETA: 10:08 - loss: 0.7704 - accuracy: 0.4375
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
  6/804 [..............................] - ETA: 12s - loss: 0.7248 - accuracy: 0.4219  
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
 12/804 [..............................] - ETA: 9s - loss: 0.7021 - accuracy: 0.5182 
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
 21/804 [..............................] - ETA: 7s - loss: 0.6934 - accuracy: 0.5640
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
 27/804 [>.............................] - ETA: 7s - loss: 0.6885 - accuracy: 0.5706
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
 31/804 [>.............................] - ETA: 7s - loss: 0.6827 - accurac

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
296/804 [==========>...................] - ETA: 4s - loss: 0.5953 - accuracy: 0.6984
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
306/804 [==========>...................] - ETA: 4s - loss: 0.5949 - accuracy: 0.6989
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
316/804 [==========>...................] - ETA: 4s - loss: 0.5937 - accuracy: 0.6999
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
326/804 [===========>..................] - ETA: 4s - loss: 0.5917 - accuracy: 0.7014
Epoch 00001: sav

601/804 [=====================>........] - ETA: 1s - loss: 0.5791 - accuracy: 0.7113
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
608/804 [=====================>........] - ETA: 1s - loss: 0.5786 - accuracy: 0.7115
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
615/804 [=====================>........] - ETA: 1s - loss: 0.5786 - accuracy: 0.7114
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
621/804 [======================>.......] - ETA: 1s - loss: 0.5786 - accuracy: 0.7113
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5
631/804 [======================>.......] - ETA: 1s - loss: 0.5779 - accuracy: 0.7117
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.01.hdf5

Epoch 00001:


Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
112/804 [===>..........................] - ETA: 5s - loss: 0.5543 - accuracy: 0.7288
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
122/804 [===>..........................] - ETA: 5s - loss: 0.5490 - accuracy: 0.7326
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
132/804 [===>..........................] - ETA: 5s - loss: 0.5499 - accuracy: 0.7325
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
141/804 [====>.........................] - ETA: 4s - loss: 0.5491 - accuracy: 0.7334
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
144/804 [====>.........................] - ETA: 5s - loss: 0.5488 - accuracy: 0.7333
Epoch 00002:

415/804 [==============>...............] - ETA: 3s - loss: 0.5505 - accuracy: 0.7300
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
422/804 [==============>...............] - ETA: 3s - loss: 0.5506 - accuracy: 0.7296
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
427/804 [==============>...............] - ETA: 3s - loss: 0.5498 - accuracy: 0.7300
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
432/804 [===============>..............] - ETA: 3s - loss: 0.5504 - accuracy: 0.7295
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
440/804 [===============>..............] - ETA: 3s - loss: 0.5500 - accuracy: 0.7300
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.02.hdf5
445/804 [===============>..............] - ETA: 3s - loss: 0.5497 - accuracy: 0.7302
Epoch 000

...

384/804 [=============>................] - ETA: 3s - loss: 0.5359 - accuracy: 0.7385
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
394/804 [=============>................] - ETA: 3s - loss: 0.5360 - accuracy: 0.7385
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
404/804 [==============>...............] - ETA: 3s - loss: 0.5358 - accuracy: 0.7393
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
414/804 [==============>...............] - ETA: 3s - loss: 0.5361 - accuracy: 0.7392
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
423/804 [==============>...............] - ETA: 3s - loss: 0.5359 - accuracy: 0.7397
Epoch 00099:

694/804 [========================>.....] - ETA: 0s - loss: 0.5356 - accuracy: 0.7398
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
703/804 [=========================>....] - ETA: 0s - loss: 0.5352 - accuracy: 0.7400
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
709/804 [=========================>....] - ETA: 0s - loss: 0.5356 - accuracy: 0.7400
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
716/804 [=========================>....] - ETA: 0s - loss: 0.5351 - accuracy: 0.7403
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5
724/804 [==========================>...] - ETA: 0s - loss: 0.5347 - accuracy: 0.7406
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.99.hdf5

Epoch 00099:

175/804 [=====>........................] - ETA: 5s - loss: 0.5409 - accuracy: 0.7355
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
184/804 [=====>........................] - ETA: 5s - loss: 0.5409 - accuracy: 0.7362
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
190/804 [======>.......................] - ETA: 5s - loss: 0.5412 - accuracy: 0.7357
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
198/804 [======>.......................] - ETA: 5s - loss: 0.5391 - accuracy: 0.7372
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
203/804 [======>.......................] - ETA: 5s - loss: 0.5379 - accuracy: 0.7386
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
210/80

465/804 [================>.............] - ETA: 3s - loss: 0.5358 - accuracy: 0.7401
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
478/804 [================>.............] - ETA: 3s - loss: 0.5353 - accuracy: 0.7405
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
480/804 [================>.............] - ETA: 3s - loss: 0.5354 - accuracy: 0.7402
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
485/804 [=================>............] - ETA: 2s - loss: 0.5353 - accuracy: 0.7404
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
490/804 [=================>............] - ETA: 2s - loss: 0.5351 - accuracy: 0.7407
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
499/804 [=================>............] - ETA: 2s - loss: 0.5348 - accuracy: 0.7412
Epo

766/804 [===========================>..] - ETA: 0s - loss: 0.5349 - accuracy: 0.7401
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
775/804 [===========================>..] - ETA: 0s - loss: 0.5351 - accuracy: 0.7400
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
783/804 [============================>.] - ETA: 0s - loss: 0.5353 - accuracy: 0.7401
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
790/804 [============================>.] - ETA: 0s - loss: 0.5351 - accuracy: 0.7402
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt2/weights.100.hdf5
800/804 [============================>.] - ETA: 0s - loss: 0.5345 - accuracy: 0.7407
Epoch

In [25]:
# Evaluate the model using the test data
model_loss, model_accuracy = nn_new.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

268/268 - 0s - loss: 0.5545 - accuracy: 0.7245
Loss: 0.5544705390930176, Accuracy: 0.7245481014251709


### Third attempt for > 75% accuracy: 
- Will keep the new bins
- Will keep the third hidden layer
- Third attempt will add 100 epochs, so total epochs will be 200

In [26]:
# Define the model - deep neural net, i.e., the number of input features and hidden nodes for each layer.
number_input_features = len(X_train_scaled[0])
hidden_nodes_layer1 = 80
hidden_nodes_layer2 = 30
hidden_nodes_layer3 = 10

nn_new1 = tf.keras.models.Sequential()

# First hidden layer
nn_new1.add(tf.keras.layers.Dense(units=hidden_nodes_layer1, activation='relu', input_dim=number_input_features))

# Second hidden layer
nn_new1.add(tf.keras.layers.Dense(units=hidden_nodes_layer2, activation='relu'))

# Third hidden layer
nn_new1.add(tf.keras.layers.Dense(units=hidden_nodes_layer3, activation='relu'))

# Output layer
nn_new1.add(tf.keras.layers.Dense(units=1, activation='sigmoid'))

# Check the structure of the model
nn_new1.summary()

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 80)                3680      
_________________________________________________________________
dense_8 (Dense)              (None, 30)                2430      
_________________________________________________________________
dense_9 (Dense)              (None, 10)                310       
_________________________________________________________________
dense_10 (Dense)             (None, 1)                 11        
Total params: 6,431
Trainable params: 6,431
Non-trainable params: 0
_________________________________________________________________


In [27]:
# Define the checkpoint path and filenames
os.makedirs("Alphabet_checkpoints/Alphabet_Opt3",exist_ok=True)
checkpoint_path = "Alphabet_checkpoints/Alphabet_Opt3/weights.{epoch:02d}.hdf5"

In [28]:
# Compile the model
nn_new1.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

# Create callback to save model weights every 5 epochs
cp_callback = ModelCheckpoint(
    filepath=checkpoint_path,
    verbose=1,
    save_weights_only=True,
    save_freq = 5
)

In [29]:
# Train the model
fit_model = nn_new1.fit(X_train_scaled,y_train,epochs=100,callbacks=[cp_callback])

Epoch 1/100
  1/804 [..............................] - ETA: 10:16 - loss: 0.7624 - accuracy: 0.4062
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
  6/804 [..............................] - ETA: 8s - loss: 0.7302 - accuracy: 0.5104   
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
 16/804 [..............................] - ETA: 6s - loss: 0.6997 - accuracy: 0.5820
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
 25/804 [..............................] - ETA: 5s - loss: 0.6884 - accuracy: 0.5900
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
 31/804 [>.............................] - ETA: 5s - loss: 0.6835 - accuracy: 0.6099
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.

297/804 [==========>...................] - ETA: 4s - loss: 0.5892 - accuracy: 0.7131
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
306/804 [==========>...................] - ETA: 4s - loss: 0.5870 - accuracy: 0.7148
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
316/804 [==========>...................] - ETA: 4s - loss: 0.5864 - accuracy: 0.7139
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
325/804 [===========>..................] - ETA: 4s - loss: 0.5856 - accuracy: 0.7140
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
331/804 [===========>..................] - ETA: 4s - loss: 0.5847 - accuracy: 0.7150
Epoch 00001:

606/804 [=====================>........] - ETA: 1s - loss: 0.5762 - accuracy: 0.7190
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
616/804 [=====================>........] - ETA: 1s - loss: 0.5755 - accuracy: 0.7195
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
622/804 [======================>.......] - ETA: 1s - loss: 0.5752 - accuracy: 0.7196
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
626/804 [======================>.......] - ETA: 1s - loss: 0.5754 - accuracy: 0.7194
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5
636/804 [======================>.......] - ETA: 1s - loss: 0.5747 - accuracy: 0.7198
Epoch 00001: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.01.hdf5

Epoch 00001:

117/804 [===>..........................] - ETA: 5s - loss: 0.5641 - accuracy: 0.7204
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
127/804 [===>..........................] - ETA: 4s - loss: 0.5654 - accuracy: 0.7190
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
136/804 [====>.........................] - ETA: 4s - loss: 0.5656 - accuracy: 0.7199
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
142/804 [====>.........................] - ETA: 4s - loss: 0.5654 - accuracy: 0.7190
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
152/804 [====>.........................] - ETA: 4s - loss: 0.5648 - accuracy: 0.7210
Epoch 00002:

417/804 [==============>...............] - ETA: 3s - loss: 0.5546 - accuracy: 0.7304
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
425/804 [==============>...............] - ETA: 3s - loss: 0.5547 - accuracy: 0.7304
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
432/804 [===============>..............] - ETA: 2s - loss: 0.5535 - accuracy: 0.7315
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
442/804 [===============>..............] - ETA: 2s - loss: 0.5528 - accuracy: 0.7323
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5
447/804 [===============>..............] - ETA: 2s - loss: 0.5529 - accuracy: 0.7319
Epoch 00002: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.02.hdf5

Epoch 00002:

...

319/804 [==========>...................] - ETA: 4s - loss: 0.5296 - accuracy: 0.7436
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
325/804 [===========>..................] - ETA: 4s - loss: 0.5301 - accuracy: 0.7434
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
329/804 [===========>..................] - ETA: 4s - loss: 0.5299 - accuracy: 0.7435
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
335/804 [===========>..................] - ETA: 4s - loss: 0.5295 - accuracy: 0.7443
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
344/804 [===========>..................] - ETA: 4s - loss: 0.5291 - accuracy: 0.7445
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
354/804 [====

624/804 [======================>.......] - ETA: 1s - loss: 0.5300 - accuracy: 0.7429
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
629/804 [======================>.......] - ETA: 1s - loss: 0.5300 - accuracy: 0.7427
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
639/804 [======================>.......] - ETA: 1s - loss: 0.5302 - accuracy: 0.7423
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
649/804 [=======================>......] - ETA: 1s - loss: 0.5305 - accuracy: 0.7423
Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5

Epoch 00099: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.99.hdf5
659/804 [=======================>......] - ETA: 1s - loss: 0.5308 - accuracy: 0.7421
Epoch 00099:

130/804 [===>..........................] - ETA: 5s - loss: 0.5341 - accuracy: 0.7404
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
140/804 [====>.........................] - ETA: 5s - loss: 0.5347 - accuracy: 0.7397
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
150/804 [====>.........................] - ETA: 5s - loss: 0.5318 - accuracy: 0.7417
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
160/804 [====>.........................] - ETA: 4s - loss: 0.5348 - accuracy: 0.7396
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
170/804 

429/804 [===============>..............] - ETA: 3s - loss: 0.5347 - accuracy: 0.7406
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
435/804 [===============>..............] - ETA: 3s - loss: 0.5347 - accuracy: 0.7409
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
444/804 [===============>..............] - ETA: 3s - loss: 0.5351 - accuracy: 0.7406
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
450/804 [===============>..............] - ETA: 3s - loss: 0.5356 - accuracy: 0.7399
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
459/804 [================>.............] - ETA: 3s - loss: 0.5355 - accuracy: 0.7394
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch

720/804 [=========================>....] - ETA: 0s - loss: 0.5332 - accuracy: 0.7414
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
725/804 [==========================>...] - ETA: 0s - loss: 0.5329 - accuracy: 0.7418
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
735/804 [==========================>...] - ETA: 0s - loss: 0.5333 - accuracy: 0.7418
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
745/804 [==========================>...] - ETA: 0s - loss: 0.5328 - accuracy: 0.7423
Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5

Epoch 00100: saving model to Alphabet_checkpoints/Alphabet_Opt3/weights.100.hdf5
755/804 [===========================>..] - ETA: 0s - loss: 0.5324 - accuracy: 0.7426
Epoch

In [30]:
# Evaluate the model using the test data
model_loss, model_accuracy = nn_new1.evaluate(X_test_scaled,y_test,verbose=2)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

268/268 - 0s - loss: 0.5562 - accuracy: 0.7263
Loss: 0.5562294125556946, Accuracy: 0.7262973785400391


In [31]:
# Save and export results
nn.save('AlphabetSoupCharity_Optimization1.h5')
nn_new.save('AlphabetSoupCharity_Optimization2.h5')
nn_new1.save('AlphabetSoupCharity_Optimization3.h5')

### Failed all 3 attempts
- All attempts ended with the accuracy going down